In [56]:
import os, sys
# enable absolute paths transversal (from notebooks folder to src folder)
parent_dir = os.path.abspath('..')
if parent_dir not in sys.path:
    sys.path.append(parent_dir)
    
from datetime import datetime, timedelta
import streamlit as st

import src.utils as utils
import src.portfolio.calculate as calculate
import src.portfolio.plot as plot

tickers = ['AAPL','AMZN','NVDA','MMC','GOOG','MSFT','BTC-USD','ETH-USD','XOM','BAC','V','GOLD','^GSPC']
start_date = '2014-01-01'
end_date = datetime.now() - timedelta(1)

# just grabbing the 'Adj Close' column
stock_data = utils.get_stock_data(tickers, start_date, end_date)
stock_data.head()

2023-06-01 11:42:05,984 (INFO):  utils.get_stock_data - Getting stock data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


[*********************100%***********************]  13 of 13 completed


AAPL       AMZN        BAC  BTC-USD  ETH-USD       GOLD   
Date                                                                       
2014-01-02  17.364964  19.898500  13.633099      NaN      NaN  15.584034  \
2014-01-03  16.983534  19.822001  13.895598      NaN      NaN  15.447858   
2014-01-06  17.076138  19.681499  14.107294      NaN      NaN  15.618079   
2014-01-07  16.954018  19.901501  13.971807      NaN      NaN  15.549994   
2014-01-08  17.061382  20.096001  14.039550      NaN      NaN  15.286140   

                 GOOG        MMC       MSFT      NVDA          V        XOM   
Date                                                                          
2014-01-02  27.724083  40.093502  31.420710  3.741748  51.729675  66.009567  \
2014-01-03  27.521841  40.202721  31.209324  3.696921  51.764778  65.850746   
2014-01-06  27.828691  39.992672  30.549797  3.746466  51.453476  65.950012   
2014-01-07  28.365179  40.278339  30.786541  3.807806  51.846699  66.883095   
2014-01-08  28.424210  40.454769  30.236942  3.859708  52.012890  66.664696   

                  ^GSPC  
Date                     
2014-01-02  1831.979980  
2014-01-03  1831.369995  
2014-01-06  1826.770020  
2014-01-07  1837.880005  
2014-01-08  1837.489990

In [57]:
stock_data.describe()


AAPL         AMZN          BAC       BTC-USD      ETH-USD   
count  2368.000000  2368.000000  2368.000000   3178.000000  2029.000000  \
mean     69.435490    81.215652    24.417959  13435.048973  1172.417127   
std      51.560236    51.275883     9.252867  16026.074464  1154.185473   
min      15.690092    14.347500     9.634965    178.102997    84.308296   
25%      26.921909    34.665876    14.639809    741.144989   219.848511   
50%      44.278107    83.167252    24.549141   7513.029541   621.859985   
75%     123.476412   115.372375    30.423261  19532.446777  1806.971802   
max     180.434296   186.570496    47.945427  67566.828125  4812.087402   

              GOLD         GOOG          MMC         MSFT         NVDA   
count  2368.000000  2368.000000  2368.000000  2368.000000  2368.000000  \
mean     15.288963    65.143206    91.163471   133.026428    78.653597   
std       4.592784    34.885039    41.237309    93.055583    81.729998   
min       5.175686    24.560070    37.506302    29.577414     3.623785   
25%      11.772255    36.954000    56.338223    48.573588     9.050351   
50%      15.248911    55.278500    77.330101   100.514648    47.390116   
75%      18.122096    88.979748   112.521439   220.963375   132.348015   
max      27.830776   150.709000   181.589996   338.335938   401.109985   

                 V          XOM        ^GSPC  
count  2368.000000  2368.000000  2368.000000  
mean    136.480234    62.826737  2916.054679  
std      62.705350    16.678196   851.289109  
min      46.106236    26.335979  1741.890015  
25%      74.624807    56.542541  2108.500061  
50%     133.615181    60.704004  2744.035034  
75%     198.991066    64.838936  3710.617432  
max     247.302551   117.321945  4796.560059


some resources:

https://www.allthesnippets.com/notes/finance/calculating_cumulative_returns_of_stocks_with_python_and_pandas.html

https://www.codingfinance.com/

https://builtin.com/data-science/portfolio-optimization-python

https://pyportfolioopt.readthedocs.io/en/latest/index.html#

In [58]:
# the cumulative return over the entire period can be computed by calculating the percentage change between the first and last values of the series
# the lambda is just a function that is applied to each column of the dataframe to ensure that the first and last values are not null
# we basically want this: cum_return = (df1.iloc[-1] - df1.iloc[0]) / df1.iloc[0] * 100
# this is a simple return on investment calculation
cumulative_return_entire_period = (stock_data.apply(lambda x: x[x.last_valid_index()]) - stock_data.apply(lambda x: x[x.first_valid_index()])) / stock_data.apply(lambda x: x[x.first_valid_index()]) * 100

# apply a percentage format to the entire series
cumulative_return_entire_period = cumulative_return_entire_period.apply(lambda x: "{:.2f}%".format(x))
print(f'cumulative return entire period: (%) \n{cumulative_return_entire_period}')

cumulative return entire period: (%) 
AAPL         921.02%
AMZN         511.40%
BAC          107.29%
BTC-USD     5957.36%
ETH-USD      492.43%
GOLD           7.67%
GOOG         349.57%
MMC          334.78%
MSFT         954.11%
NVDA       10619.86%
V            328.46%
XOM           57.61%
^GSPC        129.56%
dtype: object


In [59]:


# This method, cumulative product of returns, takes into account the compounding effect where the gains/losses from one day will affect the returns on the following day
cumulative_daily_returns = (1 + stock_data.pct_change()).cumprod() - 1
cumulative_daily_returns.reset_index(inplace=True)
print(f'last row of cum daily returns {cumulative_daily_returns.tail(5)}')

# [-1,1:] means last row, and all columns except the first one (date)
print(f'last row of cum daily returns as a %\n{(cumulative_daily_returns.iloc[-1,1:]*100).apply(lambda x: "{:.2f}%".format(x))}')


# Both methods can be useful depending on the context and what you want to analyze. For instance, if you are analyzing the total return over a 
# multi-year period for a buy and hold strategy, the simple return method may suffice.However, if you want to look at the return characteristics 
# and the compounding effect in more detail, the cumulative product method might be more appropriate.

last row of cum daily returns            Date      AAPL      AMZN       BAC    BTC-USD   ETH-USD      GOLD   
3351 2023-05-26  9.102526  5.036133  1.076564  57.424019  4.698912  0.083802  \
3352 2023-05-27  9.102526  5.036133  1.076564  57.749957  4.706480  0.083802   
3353 2023-05-28  9.102526  5.036133  1.076564  60.411672  4.955156  0.083802   
3354 2023-05-29  9.102526  5.036133  1.076564  59.668754  4.899572  0.083802   
3355 2023-05-30  9.210215  5.114029  1.072896  59.573560  4.924342  0.076743   

          GOOG       MMC      MSFT        NVDA         V       XOM     ^GSPC  
3351  3.524225  3.320650  9.594605  103.085044  3.349728  0.590224  1.295577  
3352  3.524225  3.320650  9.594605  103.085044  3.349728  0.590224  1.295577  
3353  3.524225  3.320650  9.594605  103.085044  3.349728  0.590224  1.295577  
3354  3.524225  3.320650  9.594605  103.085044  3.349728  0.590224  1.295577  
3355  3.495730  3.347837  9.541137  106.198561  3.284581  0.576135  1.295615  
last row of cum

In [60]:
cumulative_daily_returns = utils.calculate_cumulative_daily_returns(stock_data)
#print(f'last row of cum daily returns as a %\n{(cumulative_daily_returns.iloc[-1,1:]*100).apply(lambda x: "{:.2f}%".format(x))}')
print(f'last row of cum daily returns\n{cumulative_daily_returns.iloc[-1,1:]}')
print(f'tail of cum daily returns\n{cumulative_daily_returns.tail(5)}')
print(f'cumulative_daily_returns.columns[:,1:]*100\n: {cumulative_daily_returns.iloc[:,1:]*100}')

import plotly.graph_objects as go
import plotly.express as px


fig = go.Figure()

# Iterate over each column (excluding the 'Date' column)
for column in cumulative_daily_returns.columns[1:]:
    fig.add_trace(go.Scatter(
        x=cumulative_daily_returns['Date'], 
        y=cumulative_daily_returns[column],  # multiply by 100 if you want to express the returns in percentages
        mode='lines',
        name=column
    ))
# AHHH... if using tickformat, do not multiply returns by 100
fig.update_yaxes(title_text='Cumulative Returns (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Daily Returns')
fig.show()

last row of cum daily returns
AAPL         9.210215
AMZN         5.114029
BAC          1.072896
BTC-USD      59.57356
ETH-USD      4.924342
GOLD         0.076743
GOOG          3.49573
MMC          3.347837
MSFT         9.541137
NVDA       106.198561
V            3.284581
XOM          0.576135
^GSPC        1.295615
Name: 3355, dtype: object
tail of cum daily returns
           Date      AAPL      AMZN       BAC    BTC-USD   ETH-USD      GOLD   
3351 2023-05-26  9.102526  5.036133  1.076564  57.424019  4.698912  0.083802  \
3352 2023-05-27  9.102526  5.036133  1.076564  57.749957  4.706480  0.083802   
3353 2023-05-28  9.102526  5.036133  1.076564  60.411672  4.955156  0.083802   
3354 2023-05-29  9.102526  5.036133  1.076564  59.668754  4.899572  0.083802   
3355 2023-05-30  9.210215  5.114029  1.072896  59.573560  4.924342  0.076743   

          GOOG       MMC      MSFT        NVDA         V       XOM     ^GSPC  
3351  3.524225  3.320650  9.594605  103.085044  3.349728  0.590224  1.29

In [61]:
mean_monthly_returns = stock_data.pct_change().resample('M').mean()
print(f'mean_monthly_returns tail:\n{mean_monthly_returns.iloc[-1,1:]}')
print(f'keys: {mean_monthly_returns.keys()}')

fig = go.Figure()
# Iterate over each column (excluding the 'Date' column)
for column in mean_monthly_returns.columns[1:]:
    fig.add_trace(go.Scatter(
        x=mean_monthly_returns.index, 
        y=mean_monthly_returns[column], 
        mode='lines',
        name=column
    ))
    
fig.update_yaxes(title_text='Mean Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Mean Monthly Returns')
fig.show()

cumulative_mean_monthly_returns = (1 + mean_monthly_returns).cumprod() - 1
print(f'mean_monthly_returns tail:\n{cumulative_mean_monthly_returns.iloc[-1,1:]}')

fig = go.Figure()

# Iterate over each column (excluding the 'Date' column)
for column in cumulative_mean_monthly_returns.columns[1:]:
    fig.add_trace(go.Scatter(
        x=cumulative_mean_monthly_returns.index, 
        y=cumulative_mean_monthly_returns[column], 
        mode='lines',
        name=column
    ))

fig.update_yaxes(title_text='Cumulative Mean Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Mean Returns')
fig.show()


monthly_returns = stock_data.pct_change().resample('M').apply(lambda x: (1 + x).prod() - 1)
print(f'monthly_returns tail:\n{monthly_returns.iloc[-1,1:]}')

fig = go.Figure()
for column in monthly_returns.columns[1:]:
    fig.add_trace(go.Scatter(
        x=monthly_returns.index, 
        y=monthly_returns[column],  
        mode='lines',
        name=column
    ))
    
fig.update_yaxes(title_text='Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Monthly Returns')
fig.show()

cumulative_monthly_returns = (1 + monthly_returns).cumprod() - 1
print(f'cumulative_monthly_returns tail:\n{cumulative_monthly_returns.iloc[-1,1:]}')

fig = go.Figure()
for column in cumulative_monthly_returns.columns[1:]:
    fig.add_trace(go.Scatter(
        x=cumulative_monthly_returns.index,
        y=cumulative_monthly_returns[column],  
        mode='lines',
        name=column
    ))
    
fig.update_yaxes(title_text='Cumulative Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Monthly Returns')
fig.show()

sp500_monthly_returns = stock_data['^GSPC'].pct_change().resample('M').apply(lambda x: (1 + x).prod() - 1)
sp500_cumulative_monthly_returns = (1 + sp500_monthly_returns).cumprod() - 1

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=sp500_cumulative_monthly_returns.index,
    y=sp500_cumulative_monthly_returns,
    mode='lines',
    name='S&P 500'
))

fig.update_yaxes(title_text='S&P 500 - Cumulative Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='S&P 500 - Cumulative Monthly Returns')
fig.show()


mean_monthly_returns tail:
AMZN       0.004893
BAC       -0.001079
BTC-USD   -0.001676
ETH-USD    0.000635
GOLD      -0.003889
GOOG       0.004825
MMC       -0.001074
MSFT       0.002633
NVDA       0.013321
V         -0.001512
XOM       -0.003896
^GSPC      0.000309
Name: 2023-05-31 00:00:00, dtype: float64
keys: Index(['AAPL', 'AMZN', 'BAC', 'BTC-USD', 'ETH-USD', 'GOLD', 'GOOG', 'MMC',
       'MSFT', 'NVDA', 'V', 'XOM', '^GSPC'],
      dtype='object')


mean_monthly_returns tail:
AMZN       0.076078
BAC        0.040557
BTC-USD    0.224270
ETH-USD    0.152752
GOLD       0.025841
GOOG       0.062993
MMC        0.058655
MSFT       0.096400
NVDA       0.209678
V          0.058883
XOM        0.027577
^GSPC      0.034050
Name: 2023-05-31 00:00:00, dtype: float64


monthly_returns tail:
AMZN       0.153722
BAC       -0.034836
BTC-USD   -0.053520
ETH-USD    0.012841
GOLD      -0.113480
GOOG       0.151728
MMC       -0.032577
MSFT       0.080303
NVDA       0.445494
V         -0.045795
XOM       -0.113209
^GSPC      0.008644
Name: 2023-05-31 00:00:00, dtype: float64


cumulative_monthly_returns tail:
AMZN         5.114029
BAC          1.072896
BTC-USD     59.573560
ETH-USD      4.924342
GOLD         0.076743
GOOG         3.495730
MMC          3.347837
MSFT         9.541137
NVDA       106.198561
V            3.284581
XOM          0.576135
^GSPC        1.295615
Name: 2023-05-31 00:00:00, dtype: float64


In [62]:
import plotly.graph_objects as go
import plotly.express as px

#Calculating the relative cumulative monthly return for each stock compared to the S&P 500:

# First, calculate the monthly returns for each stock and the S&P 500
monthly_returns = stock_data.pct_change().resample('M').apply(lambda x: (1 + x).prod() - 1)

# Then, calculate the cumulative monthly returns
cumulative_monthly_returns = (1 + monthly_returns).cumprod() - 1
print(f'cumulative_monthly_returns tail:\n{cumulative_monthly_returns.iloc[-1,1:]}')
print(f'keys: {cumulative_monthly_returns.keys()}')

fig = go.Figure()
for column in cumulative_monthly_returns.keys():
    fig.add_trace(go.Scatter(
        x=cumulative_monthly_returns.index,
        y=cumulative_monthly_returns[column],  
        mode='lines',
        name=column
    ))
    

fig.update_yaxes(title_text='Cumulative Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Monthly Returns')
fig.show()

fig = go.Figure()
for column in cumulative_monthly_returns.keys():
    fig.add_trace(go.Scatter(
        x=cumulative_monthly_returns.index,
        y=cumulative_monthly_returns[column],  
        mode='lines',
        name=column
    ))
    

fig.update_yaxes(title_text='Cumulative Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Monthly Returns (log scale)', yaxis_type='log')
fig.show()

# Calculate the cumulative monthly returns for the S&P 500
sp500_cumulative_monthly_returns = cumulative_monthly_returns['^GSPC']
print(f'cumulative_monthly_returns tail:\n{sp500_cumulative_monthly_returns.iloc[-1]}')

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=sp500_cumulative_monthly_returns.index,
    y=sp500_cumulative_monthly_returns,
    mode='lines',
    name='S&P 500'
))

fig.update_yaxes(title_text='S&P 500 - Cumulative Monthly Returns (%)', tickformat=".1%")
fig.update_layout(title='S&P 500 - Cumulative Monthly Returns')
fig.show()


# Then, subtract the S&P 500 cumulative returns from each stock's cumulative returns
relative_cumulative_monthly_returns = cumulative_monthly_returns.subtract(sp500_cumulative_monthly_returns, axis=0)
print(f'cumulative_monthly_returns tail:\n{relative_cumulative_monthly_returns.iloc[-1,1:]}')

fig = go.Figure()
for column in relative_cumulative_monthly_returns.keys():
    fig.add_trace(go.Scatter(
        x=relative_cumulative_monthly_returns.index,
        y=relative_cumulative_monthly_returns[column],  
        mode='lines',
        name=column
    ))
    

fig.update_yaxes(title_text='Cumulative Monthly Returns Relative to S&P500 (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Monthly Returns Relative to S&P500')
fig.show()


mean_monthly_returns = stock_data.pct_change().resample('M').mean()
sp500_mean_monthly_returns = mean_monthly_returns['^GSPC']

mean_monthly_returns.drop('^GSPC', axis=1, inplace=True)

relative_mean_monthly_returns = mean_monthly_returns.subtract(sp500_mean_monthly_returns, axis=0)

fig = go.Figure()
for column in relative_mean_monthly_returns.keys():
    cumulative_mean_monthly_returns_relative_to_sp500 = (1 + relative_mean_monthly_returns[column]).cumprod() - 1
    fig.add_trace(go.Scatter(
        x=cumulative_mean_monthly_returns_relative_to_sp500.index,
        y=cumulative_mean_monthly_returns_relative_to_sp500,
        mode='lines',
        name=column
    ))
    
fig.update_yaxes(title_text='Cumulative Mean Monthly Returns Relative to S&P500 (%)', tickformat=".1%")
fig.update_layout(title='Cumulative Mean Monthly Returns Relative to S&P500')
fig.show()



cumulative_monthly_returns tail:
AMZN         5.114029
BAC          1.072896
BTC-USD     59.573560
ETH-USD      4.924342
GOLD         0.076743
GOOG         3.495730
MMC          3.347837
MSFT         9.541137
NVDA       106.198561
V            3.284581
XOM          0.576135
^GSPC        1.295615
Name: 2023-05-31 00:00:00, dtype: float64
keys: Index(['AAPL', 'AMZN', 'BAC', 'BTC-USD', 'ETH-USD', 'GOLD', 'GOOG', 'MMC',
       'MSFT', 'NVDA', 'V', 'XOM', '^GSPC'],
      dtype='object')


cumulative_monthly_returns tail:
1.2956146160806807


cumulative_monthly_returns tail:
AMZN         3.818414
BAC         -0.222718
BTC-USD     58.277946
ETH-USD      3.628727
GOLD        -1.218872
GOOG         2.200116
MMC          2.052222
MSFT         8.245522
NVDA       104.902946
V            1.988967
XOM         -0.719479
^GSPC        0.000000
Name: 2023-05-31 00:00:00, dtype: float64


In [63]:
from pypfopt import expected_returns, EfficientFrontier
import numpy as np
import pandas as pd
import src.rebalancing.calculate as r_calculate

risk_free_rate = 0.04
mu = expected_returns.mean_historical_return(stock_data)
S = utils.calculate_covariance_matrix(stock_data)

# Calculating the cumulative monthly returns of a portfolio of stocks with given weights:
min_risk, max_risk = utils.calculate_risk_extents(mu, S, risk_free_rate)
risk = (max_risk + min_risk) / 2

ef = EfficientFrontier(mu, S)
ef.efficient_risk(risk)
weights = ef.clean_weights()
weights = pd.Series(weights).reindex(stock_data.columns)
ef_returns, ef_volatility, ef_sharpe = ef.portfolio_performance(risk_free_rate)
print(f'ef weights:\n{weights}')
print(f'ef performance: {ef_returns, ef_volatility, ef_sharpe}')

ef_min_v = EfficientFrontier(mu, S)
min_volatility_portfolio_weights = ef_min_v.min_volatility()
weights_min_v = ef_min_v.clean_weights()
weights_min_v = pd.Series(weights_min_v).reindex(stock_data.columns)
min_v_returns, min_v_volatility, min_v_sharpe = ef_min_v.portfolio_performance(risk_free_rate)
print(f'min v weights:\n{weights_min_v}')
print(f'min_v performance: {min_v_returns, min_v_volatility, min_v_sharpe}')

ef_max_sharpe = EfficientFrontier(mu, S)
max_sharpe_portfolio_weights = ef_max_sharpe.max_sharpe(risk_free_rate)
weights_max_sharpe = ef_max_sharpe.clean_weights()
weights_max_sharpe = pd.Series(weights_max_sharpe).reindex(stock_data.columns)
max_sharpe_returns, max_sharpe_volatility, max_sharpe = ef_max_sharpe.portfolio_performance(risk_free_rate)
print(f'max sharpe weights:\n{weights_max_sharpe}')
print(f'max sharpe performance: {max_sharpe_returns, max_sharpe_volatility, max_sharpe}')
    
#weights = utils.calculate_optimal_portfolio(stock_data, risk_free_rate=0.04)

# First, calculate the daily returns for each stock
daily_returns = stock_data.pct_change()
print(f'daily_returns tail:\n{daily_returns.tail()}')

# Calculate the weighted returns
weighted_returns = daily_returns.multiply(weights, axis=1)

# Then, calculate the portfolio return by summing across the rows (i.e., the weighted returns for each day)
portfolio_returns = weighted_returns.sum(axis=1)
print(f'portfolio_returns tail:\n{portfolio_returns.tail()}')

# Resample the portfolio returns into monthly returns
portfolio_returns_monthly = portfolio_returns.resample('M').apply(lambda x: (1 + x).prod() - 1)

# Finally, calculate the cumulative monthly returns
portfolio_cumulative_monthly_returns = (1 + portfolio_returns_monthly).cumprod() - 1
print(f'portfolio_returns tail:\n{portfolio_cumulative_monthly_returns.tail()}')


fig = go.Figure()
fig.add_trace(go.Scatter(
    x=portfolio_cumulative_monthly_returns.index,
    y=portfolio_cumulative_monthly_returns,
    mode='lines',
    name='Weighted Portfolio'
))

fig.update_yaxes(title_text='Returns (%)', tickformat=".1%")
fig.update_layout(title='Weighted Portfolio Cumulative Monthly Returns')
fig.show()


Expected annual return: 27.8%
Annual volatility: 23.1%
Sharpe Ratio: 1.12
ef weights:
AAPL       0.11212
AMZN       0.00000
BAC        0.00000
BTC-USD    0.15095
ETH-USD    0.00000
GOLD       0.00000
GOOG       0.00000
MMC        0.29396
MSFT       0.09612
NVDA       0.34684
V          0.00000
XOM        0.00000
^GSPC      0.00000
dtype: float64
ef performance: (0.2782702973694775, 0.23117139849051604, 1.1172242719294412)
Expected annual return: 7.4%
Annual volatility: 14.2%
Sharpe Ratio: 0.38
min v weights:
AAPL       0.00000
AMZN       0.00000
BAC        0.00000
BTC-USD    0.01471
ETH-USD    0.00000
GOLD       0.12210
GOOG       0.00000
MMC        0.25745
MSFT       0.00000
NVDA       0.00000
V          0.00000
XOM        0.05367
^GSPC      0.55208
dtype: float64
min_v performance: (0.07380953286962491, 0.1424937581647397, 0.3776272979439191)
Expected annual return: 38.0%
Annual volatility: 32.0%
Sharpe Ratio: 1.06
max sharpe weights:
AAPL       0.07845
AMZN       0.00000
BAC        

/home/jaws/development/public/portfolio-analysis-app/.venv/lib/python3.10/site-packages/pypfopt/efficient_frontier/efficient_frontier.py:441: UserWarning:

The risk_free_rate provided to portfolio_performance is different to the one used by max_sharpe. Using the previous value.



In [64]:
# now working to handle dividends and edge cases
# specifically, some assets have dividends, some don't
# and some assets returns for some dates, but not others (eg, crypto trades weekends, some assets did not IPO until later)
import pandas as pd

stock_data, dividend_data = utils.get_stock_and_dividend_data(tickers, start_date, end_date)
stock_data.drop('^GSPC', axis=1, inplace=True)
dividend_data.drop('^GSPC', axis=1, inplace=True)

# Initialize an empty DataFrame for the portfolio returns
portfolio_returns = pd.DataFrame(index=stock_data.index)

for ticker in stock_data.columns:
    # Select the data for this ticker
    ticker_data = stock_data[ticker]
    ticker_dividend_data = dividend_data[ticker] if ticker in dividend_data.columns else None

    # Ensure both are either tz aware or tz naive
    ticker_data.index = ticker_data.index.tz_localize(None)
    if ticker_dividend_data is not None:
        ticker_dividend_data.index = ticker_dividend_data.index.tz_localize(None)

    # Drop NaN values
    ticker_data = ticker_data.dropna()
    if ticker_dividend_data is not None:
        ticker_dividend_data = ticker_dividend_data.dropna()

    # Calculate the daily returns for this ticker
    ticker_returns = ticker_data.pct_change()
    
    # Calculate the daily dividend returns for this ticker, if dividend data is available
    if ticker_dividend_data is not None:
        """
        something not right in this math as overall returns is lower than without dividends
        """
        ticker_dividend_returns = ticker_dividend_data / ticker_data.shift()
        ticker_returns += ticker_dividend_returns

    # Multiply by the weight
    ticker_returns *= weights[ticker]

    # Save the ticker returns in the portfolio returns DataFrame
    portfolio_returns[ticker] = ticker_returns
    print(f'portfolio_returns {ticker} tail:\n{portfolio_returns[ticker].tail()}')

# Sum across the tickers to get the portfolio return for each day
# default pandas behavior is to ignore NaN values effectively treating as zero
# this will deal with edge cases where some assets have returns for some dates, but not others
sum_of_portfolio_returns = portfolio_returns.sum(axis=1)

# Resample the portfolio returns into monthly returns
portfolio_returns_monthly = sum_of_portfolio_returns.resample('M').apply(lambda x: (1 + x).prod() - 1)

# Finally, calculate the cumulative monthly returns
portfolio_cumulative_monthly_returns = (1 + portfolio_returns_monthly).cumprod() - 1
print(f'portfolio_returns tail:\n{portfolio_cumulative_monthly_returns.tail()}')

fig = go.Figure()
fig.add_trace(go.Scatter(
    x=portfolio_cumulative_monthly_returns.index,
    y=portfolio_cumulative_monthly_returns,
    mode='lines',
    name='Weighted Portfolio'
))

fig.update_yaxes(title_text='Returns (%)', tickformat=".1%")
fig.update_layout(title='Weighted Portfolio Cumulative Monthly Returns (w/ Dividends)')
fig.show()


2023-06-01 11:42:10,164 (INFO):  utils.get_stock_and_dividend_data - Getting stock and dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


[*********************100%***********************]  13 of 13 completed

2023-06-01 11:42:12,476 (INFO):  utils.get_dividend_data - Getting dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31



portfolio_returns AAPL tail:
Date
2023-05-26    0.001581
2023-05-27         NaN
2023-05-28         NaN
2023-05-29         NaN
2023-05-30    0.001195
Name: AAPL, dtype: float64
portfolio_returns AMZN tail:
Date
2023-05-26    0.0
2023-05-27    NaN
2023-05-28    NaN
2023-05-29    NaN
2023-05-30    0.0
Name: AMZN, dtype: float64
portfolio_returns BAC tail:
Date
2023-05-26    0.0
2023-05-27    NaN
2023-05-28    NaN
2023-05-29    NaN
2023-05-30   -0.0
Name: BAC, dtype: float64
portfolio_returns BTC-USD tail:
Date
2023-05-26    0.001386
2023-05-27    0.000842
2023-05-28    0.006839
2023-05-29   -0.001826
2023-05-30   -0.000237
Name: BTC-USD, dtype: float64
portfolio_returns ETH-USD tail:
Date
2023-05-26    0.0
2023-05-27    0.0
2023-05-28    0.0
2023-05-29   -0.0
2023-05-30    0.0
Name: ETH-USD, dtype: float64
portfolio_returns GOLD tail:
Date
2023-05-26   -0.0
2023-05-27    NaN
2023-05-28    NaN
2023-05-29    NaN
2023-05-30   -0.0
Name: GOLD, dtype: float64
portfolio_returns GOOG tail:
Date

In [65]:
# approach #2 to handle dividends and edge cases
# specifically, some assets have dividends, some don't
# and some assets returns for some dates, but not others (eg, crypto trades weekends, some assets did not IPO until later)
import pandas as pd

stock_data, dividend_data = utils.get_stock_and_dividend_data(tickers, start_date, end_date)
stock_data.drop('^GSPC', axis=1, inplace=True)
dividend_data.drop('^GSPC', axis=1, inplace=True)

portfolio_returns_without_dividends = pd.DataFrame()
portfolio_dividend_returns = pd.DataFrame()

# Calculate the annual dividends and stock prices
annual_dividends = dividend_data.resample('Y').sum()
annual_prices = stock_data.resample('Y').mean()

# Convert to tz-naive
annual_dividends.index = annual_dividends.index.tz_localize(None)
annual_prices.index = annual_prices.index.tz_localize(None)

# Calculate the dividend yield
annual_dividend_yield = annual_dividends / annual_prices
print(f'annual_dividend_yield:\n{annual_dividend_yield}')

# Calculate the annual dividends and stock prices
monthly_dividends = dividend_data.resample('Y').sum()
monthly_prices = stock_data.resample('Y').mean()

# Convert to tz-naive
monthly_dividends.index = monthly_dividends.index.tz_localize(None)
monthly_prices.index = monthly_prices.index.tz_localize(None)

# Calculate the dividend yield
monthly_dividend_yield = monthly_dividends / monthly_prices
print(f'monthly_dividend_yield:\n{monthly_dividend_yield}')

for ticker in stock_data.columns:
    # Get the data for this ticker
    ticker_data = stock_data[ticker]
    ticker_dividend_data = dividend_data[ticker]

    # Calculate the daily returns for this ticker
    ticker_returns = ticker_data.pct_change()
    portfolio_returns_without_dividends[ticker] = ticker_returns

    # Ensure both are either tz aware or tz naive
    ticker_data.index = ticker_data.index.tz_localize(None)
    if ticker_dividend_data is not None:
        ticker_dividend_data.index = ticker_dividend_data.index.tz_localize(None)
        
    # Calculate the daily dividend returns for this ticker
    ticker_dividend_returns = ticker_dividend_data / ticker_data.shift()
    portfolio_dividend_returns[ticker] = ticker_dividend_returns

# Calculate the portfolio returns
portfolio_returns_without_dividends = portfolio_returns_without_dividends.multiply(weights, axis=1).sum(axis=1)
portfolio_dividend_returns = portfolio_dividend_returns.multiply(weights, axis=1).sum(axis=1)

# Calculate the cumulative returns
cumulative_portfolio_returns_without_dividends = (1 + portfolio_returns_without_dividends).cumprod() - 1
cumulative_portfolio_dividend_returns = (1 + portfolio_dividend_returns).cumprod() - 1

# Calculate the total cumulative returns
cumulative_total_portfolio_returns = (1 + portfolio_returns_without_dividends + portfolio_dividend_returns).cumprod() - 1

fig_div = go.Figure()
fig_ticker = go.Figure() 
fig_cum = go.Figure()

# Add traces
fig_div.add_trace(go.Scatter(
    x=cumulative_portfolio_dividend_returns.index, 
    y=cumulative_portfolio_dividend_returns,
    mode='lines',
    name='Dividend Returns'
))
# Add traces
fig_cum.add_trace(go.Scatter(
    x=cumulative_portfolio_dividend_returns.index, 
    y=cumulative_portfolio_dividend_returns,
    mode='lines',
    name='Dividend Returns'
))
# Set the title and labels
fig_div.update_layout(
    title='Cumulative Dividend Returns'
)
fig_div.update_yaxes(title_text='Returns (%)', tickformat=".1%")
fig_div.show()

fig_ticker.add_trace(go.Scatter(
    x=cumulative_portfolio_returns_without_dividends.index, 
    y=cumulative_portfolio_returns_without_dividends,
    mode='lines',
    name='Price Returns'
))
fig_cum.add_trace(go.Scatter(
    x=cumulative_portfolio_returns_without_dividends.index, 
    y=cumulative_portfolio_returns_without_dividends,
    mode='lines',
    name='Price Returns'
))
# Set the title and labels
fig_ticker.update_layout(
    title='Cumulative Ticker Returns'
)
fig_ticker.update_yaxes(title_text='Returns (%)', tickformat=".1%")
fig_ticker.show()

fig_cum.add_trace(go.Scatter(
    x=cumulative_total_portfolio_returns.index, 
    y=cumulative_total_portfolio_returns,
    mode='lines',
    name='Total Returns'
))

fig_cum.update_yaxes(title_text='Returns (%)', tickformat=".1%")

# Set the title and labels
fig_cum.update_layout(
    title='Total Cumulative Weighted Portfolio Returns w/Dividends'
)

fig_cum.show()

2023-06-01 11:42:17,411 (INFO):  utils.get_stock_and_dividend_data - Getting stock and dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


[*********************100%***********************]  13 of 13 completed


2023-06-01 11:42:19,641 (INFO):  utils.get_dividend_data - Getting dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


annual_dividend_yield:
                AAPL  AMZN       BAC  BTC-USD  ETH-USD      GOLD  GOOG   
Date                                                                     
2014-12-31  0.022473   0.0  0.008652      0.0      NaN  0.014027   0.0  \
2015-12-31  0.018678   0.0  0.014065      0.0      NaN  0.016622   0.0   
2016-12-31  0.023068   0.0  0.018619      0.0      NaN  0.005579   0.0   
2017-12-31  0.017354   0.0  0.017866      0.0      0.0  0.008133   0.0   
2018-12-31  0.015604   0.0  0.020269      0.0      0.0  0.016956   0.0   
2019-12-31  0.015033   0.0  0.024361      0.0      0.0  0.009440   0.0   
2020-12-31  0.008623   0.0  0.029153      0.0      0.0  0.013929   0.0   
2021-12-31  0.006205   0.0  0.020081      0.0      0.0  0.040360   0.0   
2022-12-31  0.005912   0.0  0.023582      0.0      0.0  0.036029   0.0   
2023-12-31  0.003019   0.0  0.007066      0.0      0.0  0.010969   0.0   

                 MMC      MSFT      NVDA         V       XOM  
Date                     

In [66]:
css_colors = ['aliceblue', 'antiquewhite', 'aqua', 'aquamarine', 'azure',
            'beige', 'bisque', 'black', 'blanchedalmond', 'blue',
            'blueviolet', 'brown', 'burlywood', 'cadetblue',
            'chartreuse', 'chocolate', 'coral', 'cornflowerblue',
            'cornsilk', 'crimson', 'cyan', 'darkblue', 'darkcyan',
            'darkgoldenrod', 'darkgray', 'darkgrey', 'darkgreen',
            'darkkhaki', 'darkmagenta', 'darkolivegreen', 'darkorange',
            'darkorchid', 'darkred', 'darksalmon', 'darkseagreen',
            'darkslateblue', 'darkslategray', 'darkslategrey',
            'darkturquoise', 'darkviolet', 'deeppink', 'deepskyblue',
            'dimgray', 'dimgrey', 'dodgerblue', 'firebrick',
            'floralwhite', 'forestgreen', 'fuchsia', 'gainsboro',
            'ghostwhite', 'gold', 'goldenrod', 'gray', 'grey', 'green',
            'greenyellow', 'honeydew', 'hotpink', 'indianred', 'indigo',
            'ivory', 'khaki', 'lavender', 'lavenderblush', 'lawngreen',
            'lemonchiffon', 'lightblue', 'lightcoral', 'lightcyan',
            'lightgoldenrodyellow', 'lightgray', 'lightgrey',
            'lightgreen', 'lightpink', 'lightsalmon', 'lightseagreen',
            'lightskyblue', 'lightslategray', 'lightslategrey',
            'lightsteelblue', 'lightyellow', 'lime', 'limegreen',
            'linen', 'magenta', 'maroon', 'mediumaquamarine',
            'mediumblue', 'mediumorchid', 'mediumpurple',
            'mediumseagreen', 'mediumslateblue', 'mediumspringgreen',
            'mediumturquoise', 'mediumvioletred', 'midnightblue',
            'mintcream', 'mistyrose', 'moccasin', 'navajowhite', 'navy',
            'oldlace', 'olive', 'olivedrab', 'orange', 'orangered',
            'orchid', 'palegoldenrod', 'palegreen', 'paleturquoise',
            'palevioletred', 'papayawhip', 'peachpuff', 'peru', 'pink',
            'plum', 'powderblue', 'purple', 'red', 'rosybrown',
            'royalblue', 'rebeccapurple', 'saddlebrown', 'salmon',
            'sandybrown', 'seagreen', 'seashell', 'sienna', 'silver',
            'skyblue', 'slateblue', 'slategray', 'slategrey', 'snow',
            'springgreen', 'steelblue', 'tan', 'teal', 'thistle', 'tomato',
            'turquoise', 'violet', 'wheat', 'white', 'whitesmoke',
            'yellow', 'yellowgreen']

In [67]:
# approach #3 to handle dividends and edge cases
import pandas as pd

# Get stock and dividend data
stock_data, dividend_data = utils.get_stock_and_dividend_data(tickers, start_date, end_date)

# Remove S&P 500 data
stock_data.drop('^GSPC', axis=1, inplace=True)
dividend_data.drop('^GSPC', axis=1, inplace=True)

# Initialize dataframes for returns
portfolio_returns_without_dividends = pd.DataFrame()
portfolio_returns_with_dividends = pd.DataFrame()

# Calculate the annual dividends and stock prices
annual_dividends = dividend_data.resample('Y').sum()
annual_prices = stock_data.resample('Y').mean()

# Convert to tz-naive
annual_dividends.index = annual_dividends.index.tz_localize(None)
annual_prices.index = annual_prices.index.tz_localize(None)

# Calculate the dividend yield
annual_dividend_yield = annual_dividends / annual_prices
print(f'annual_dividend_yield:\n{annual_dividend_yield}')

# Calculate the annual dividends and stock prices
monthly_dividends = dividend_data.resample('Y').sum()
monthly_prices = stock_data.resample('Y').mean()

# Convert to tz-naive
monthly_dividends.index = monthly_dividends.index.tz_localize(None)
monthly_prices.index = monthly_prices.index.tz_localize(None)

# Calculate the dividend yield
monthly_dividend_yield = monthly_dividends / monthly_prices
print(f'monthly_dividend_yield:\n{monthly_dividend_yield}')

fig_div = go.Figure()

for i, ticker in enumerate(monthly_dividend_yield.columns):
    fig_div.add_trace(go.Scatter(
        x=monthly_dividend_yield.index, 
        y=monthly_dividend_yield[ticker],
        mode='lines',
        name=ticker,
        line=dict(color=css_colors[i])
    ))

fig_div.update_yaxes(title_text='Monthly Yield (%)', tickformat=".1%")

# Set the title and labels
fig_div.update_layout(
    title='Dividend Yield'
)

fig_div.show()

# Calculate the daily returns for each stock in the portfolio
for ticker in stock_data.columns:
    # Get the data for this ticker
    ticker_data = stock_data[ticker]
    ticker_dividend_data = dividend_data[ticker]

    # Calculate the daily returns for this ticker without considering dividends
    ticker_returns_without_dividends = ticker_data.pct_change()
    portfolio_returns_without_dividends[ticker] = ticker_returns_without_dividends

    # Ensure both are either tz aware or tz naive
    ticker_data.index = ticker_data.index.tz_localize(None)
    if ticker_dividend_data is not None:
        ticker_dividend_data.index = ticker_dividend_data.index.tz_localize(None)
        
    # Adjust the stock prices to account for reinvestment of dividends
    # Assume that dividends are reinvested, increasing the number of shares held
    if ticker_dividend_data is not None:
        adjusted_stock_data = ticker_data.copy()
        cumulative_dividends_reinvested = (ticker_dividend_data / ticker_data).cumsum()
        adjusted_stock_data += adjusted_stock_data * cumulative_dividends_reinvested

        # Calculate the daily returns for this ticker with dividends reinvested
        ticker_returns_with_dividends = adjusted_stock_data.pct_change()
        portfolio_returns_with_dividends[ticker] = ticker_returns_with_dividends


    # Calculate the daily returns for this ticker with dividends reinvested
    ticker_returns_with_dividends = adjusted_stock_data.pct_change()
    portfolio_returns_with_dividends[ticker] = ticker_returns_with_dividends

# Calculate the weighted portfolio returns
portfolio_returns_without_dividends = portfolio_returns_without_dividends.multiply(weights, axis=1).sum(axis=1)
portfolio_returns_with_dividends = portfolio_returns_with_dividends.multiply(weights, axis=1).sum(axis=1)

# Calculate the cumulative returns
cumulative_portfolio_returns_without_dividends = (1 + portfolio_returns_without_dividends).cumprod() - 1
cumulative_portfolio_returns_with_dividends = (1 + portfolio_returns_with_dividends).cumprod() - 1


fig_cum = go.Figure()
fig_cum.add_trace(go.Scatter(
    x=cumulative_portfolio_returns_without_dividends.index, 
    y=cumulative_portfolio_returns_without_dividends,
    mode='lines',
    name='Cumulative Weighted Portfolio Returns w/o Dividends',
    line=dict(color='lightseagreen')
))

fig_cum.add_trace(go.Scatter(
    x=cumulative_portfolio_returns_with_dividends.index, 
    y=cumulative_portfolio_returns_with_dividends,
    mode='lines',
    name='Cumulative Weighted Portfolio Returns w/Dividends',
    line=dict(color='royalblue', dash='dot')
))

fig_cum.update_yaxes(title_text='Returns (%)', tickformat=".1%")

# Set the title and labels
fig_cum.update_layout(
    title='Total Cumulative Weighted Portfolio Returns'
)

2023-06-01 11:42:25,379 (INFO):  utils.get_stock_and_dividend_data - Getting stock and dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


[*********************100%***********************]  13 of 13 completed


2023-06-01 11:42:27,668 (INFO):  utils.get_dividend_data - Getting dividend data for ['AAPL', 'AMZN', 'NVDA', 'MMC', 'GOOG', 'MSFT', 'BTC-USD', 'ETH-USD', 'XOM', 'BAC', 'V', 'GOLD', '^GSPC'] from 2014-01-01 to 2023-05-31


annual_dividend_yield:
                AAPL  AMZN       BAC  BTC-USD  ETH-USD      GOLD  GOOG   
Date                                                                     
2014-12-31  0.022473   0.0  0.008652      0.0      NaN  0.014027   0.0  \
2015-12-31  0.018678   0.0  0.014065      0.0      NaN  0.016622   0.0   
2016-12-31  0.023068   0.0  0.018619      0.0      NaN  0.005579   0.0   
2017-12-31  0.017354   0.0  0.017866      0.0      0.0  0.008133   0.0   
2018-12-31  0.015604   0.0  0.020269      0.0      0.0  0.016956   0.0   
2019-12-31  0.015033   0.0  0.024361      0.0      0.0  0.009440   0.0   
2020-12-31  0.008623   0.0  0.029153      0.0      0.0  0.013929   0.0   
2021-12-31  0.006205   0.0  0.020081      0.0      0.0  0.040360   0.0   
2022-12-31  0.005912   0.0  0.023582      0.0      0.0  0.036029   0.0   
2023-12-31  0.003019   0.0  0.007066      0.0      0.0  0.010969   0.0   

                 MMC      MSFT      NVDA         V       XOM  
Date                     

In [68]:
# Calculating the relative cumulative monthly returns of a portfolio of stocks with given weights, compared to the S&P 500:

# First, calculate the relative returns as before
relative_portfolio_monthly_returns = portfolio_returns_monthly - sp500_cumulative_monthly_returns

# Then, calculate the cumulative relative returns
relative_portfolio_cumulative_monthly_returns = (1 + relative_portfolio_monthly_returns).cumprod() - 1